# CapstoneProject - CaliforniaTexas

## Section 1: Scraping data:
List of cities along with population data for Texas and California

#### Section 1.1 Importing Libraries

In [1]:
# Getting required libraries
import numpy as np # library to handle data in a vectorized manner

#import pandas as pd # library for data analsysis
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

import requests # library to handle requests 

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# uncomment this line if you haven't completed the Foursquare API lab
!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values


from bs4 import BeautifulSoup  # Library ro scarp data
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

# uncomment this line if you haven't completed the Foursquare API lab
!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


#### 1.2 Getting Data: Define the source and a function

In [22]:
# Source of Data. Add States if you want more. Should from similar website or similar column name.
urlTX = "https://www.texas-demographics.com/cities_by_population"
urlCA = "https://www.california-demographics.com/cities_by_population"

# List of States
List_TX = [urlTX, 'TX', 'US']
List_CA = [urlCA, 'CA', 'US']


statelists = {'TX': List_TX, 'CA': List_CA}
dfStates = pd.DataFrame(statelists)
dfStates  = dfStates.T
dfStates .columns = ['URL', 'State', 'Country']
dfStates 

URL State Country
TX  https://www.texas-demographics.com/cities_by_p...    TX      US
CA  https://www.california-demographics.com/cities...    CA      US

Note: : Limit the cities with population between 10000 and 250000. If neccessary, Can adjust the limits when calling the function

In [23]:
#Define the Getting and Cleaning Function
def GetCleanData(url, state, country, highlimit, lowlimit):
    
    DataAll = pd.DataFrame(columns=['City', 'Population', 'State', 'Country'])
    
    for url, state, country in zip(url, state, country):
        print(state)
            
        Tables_html = pd.read_html(url)
        Table = Tables_html[0]
        Table = Table[['City', "Population"]]

        # Add State and Country
        Table['State']=state
        Table['Country']=country
        
        # Cleaning the Table  ---------------------

        # Remove Last Row 
        Table = Table.drop(Table.tail(1).index)

        # Convert population to integer
        Table['Population'] = Table['Population'].astype(int)

        Table['Population'] = Table['Population'].astype(int)
        indexNames = Table[ (Table['Population'] >= highlimit) | (Table['Population'] <= lowlimit) ].index
        Table.drop(indexNames , inplace=True)
    
        # Appending all the Data. now this is within the for loop. Everytime loop runs create a new table and
        # append that table to DataALL. Remeber DataAll is defined outside of the for loop.
        DataAll = DataAll.append(Table)
    
    DataAll = DataAll.reset_index(drop=True)
    return(DataAll)    

In [24]:

# Running the above function for State
CityData= GetCleanData(url=dfStates['URL'],
                                   state=dfStates['State'],
                                   country=dfStates['Country'],
                                   highlimit = 250000,
                                   lowlimit =10000
                                  )

print(CityData.shape)
CityData


TX
CA
(714, 4)


City Population State Country
0                             Irving     238637    TX      US
1                            Garland     237982    TX      US
2                           Amarillo     198773    TX      US
3                      Grand Prairie     191104    TX      US
4                        Brownsville     182679    TX      US
5                           McKinney     173460    TX      US
6                             Frisco     165700    TX      US
7                           Pasadena     154193    TX      US
8                      Mesquite city     144250    TX      US
9                            Killeen     143070    TX      US
10                           McAllen     141597    TX      US
11                           Midland     135134    TX      US
12                              Waco     133964    TX      US
13                            Denton     133661    TX      US
14                        Carrollton     133438    TX      US
15                           Abilene     123676    TX      US
16                        Round Rock     120157    TX      US
17                          Beaumont     118632    TX      US
18                            Odessa     118582    TX      US
19                        Sugar Land     118182    TX      US
20                          Pearland     117867    TX      US
21                        Richardson     114402    TX      US
22                   College Station     110782    TX      US
23                     The Woodlands     109843    TX      US
24                        Lewisville     104789    TX      US
25                     Wichita Falls     104494    TX      US
26                             Tyler     103721    TX      US
27                       League City     100832    TX      US
28                        San Angelo      99634    TX      US
29                             Allen      99255    TX      US
30                          Edinburg      94019    TX      US
31                           Mission      83709    TX      US
32                             Bryan      83199    TX      US
33                          Longview      82256    TX      US
34                            Conroe      80893    TX      US
35                        Atascocita      79019    TX      US
36                             Pharr      77835    TX      US
37                           Baytown      76581    TX      US
38                     New Braunfels      74587    TX      US
39                     Missouri City      73573    TX      US
40                      Flower Mound      73252    TX      US
41                            Temple      73143    TX      US
42                        Cedar Park      72415    TX      US
43              North Richland Hills      69800    TX      US
44                         Mansfield      67492    TX      US
45                          Victoria      66939    TX      US
46                        Georgetown      66804    TX      US
47                         Harlingen      65449    TX      US
48                           Rowlett      62127    TX      US
49                        San Marcos      61751    TX      US
50                      Pflugerville      59757    TX      US
51                            Spring      58756    TX      US
52                       Port Arthur      55249    TX      US
53                            Euless      55047    TX      US
54                            DeSoto      53030    TX      US
55                         Grapevine      52486    TX      US
56                         Galveston      50039    TX      US
57                           Bedford      49306    TX      US
58                             Wylie      49248    TX      US
59                        Cedar Hill      48704    TX      US
60                        Texas City      47902    TX      US
61                           Leander      46419    TX      US
62                            Keller      46175    TX      US
63                          Burleson      44629    TX      US
64

#### Section 1.3 Adding the geocode to the cities
Use the Mapquest to get  the geopcode data.

In [25]:
# Add Mapquest credentials to run the following code
MAPQUEST_KEY = ''
MAPQUEST_SECRET = ''

In [26]:

# Getting the geocode data
for index, row in CityData.iterrows():
    location = row['City'] + "," + row['State']+ "," + row['Country']
    url = 'https://www.mapquestapi.com/geocoding/v1/address?key={}&inFormat=kvp&outFormat=json&location={}&thumbMaps=false'.format(
    MAPQUEST_KEY, 
    location)
    response = requests.get(url).json()
    CityData.at[index,'Latitude'] = response['results'][0]['locations'][0]['latLng']['lat']
    CityData.at[index,'Longitude'] = response['results'][0]['locations'][0]['latLng']['lng']
    
CityData.to_csv('CityData.csv', sep=',',index=False)


In [27]:
print(CityData.shape)
CityData

(714, 6)


City Population State Country   Latitude  \
0                             Irving     238637    TX      US  32.813879   
1                            Garland     237982    TX      US  32.914343   
2                           Amarillo     198773    TX      US  35.207009   
3                      Grand Prairie     191104    TX      US  32.745496   
4                        Brownsville     182679    TX      US  25.903046   
5                           McKinney     173460    TX      US  33.197963   
6                             Frisco     165700    TX      US  33.150660   
7                           Pasadena     154193    TX      US  29.693379   
8                      Mesquite city     144250    TX      US  30.270170   
9                            Killeen     143070    TX      US  31.117810   
10                           McAllen     141597    TX      US  26.196695   
11                           Midland     135134    TX      US  31.997433   
12                              Waco     133964    TX      US  31.556767   
13                            Denton     133661    TX      US  33.215533   
14                        Carrollton     133438    TX      US  32.975541   
15                           Abilene     123676    TX      US  32.453562   
16                        Round Rock     120157    TX      US  30.508556   
17                          Beaumont     118632    TX      US  30.086170   
18                            Odessa     118582    TX      US  31.849462   
19                        Sugar Land     118182    TX      US  29.597075   
20                          Pearland     117867    TX      US  29.563689   
21                        Richardson     114402    TX      US  32.960761   
22                   College Station     110782    TX      US  30.622373   
23                     The Woodlands     109843    TX      US  30.182039   
24                        Lewisville     104789    TX      US  33.046344   
25                     Wichita Falls     104494    TX      US  33.909760   
26                             Tyler     103721    TX      US  32.350763   
27                       League City     100832    TX      US  29.507507   
28                        San Angelo      99634    TX      US  31.463780   
29                             Allen      99255    TX      US  33.104193   
30                          Edinburg      94019    TX      US  26.299359   
31                           Mission      83709    TX      US  26.212384   
32                             Bryan      83199    TX      US  30.670524   
33                          Longview      82256    TX      US  32.494556   
34                            Conroe      80893    TX      US  30.313044   
35                        Atascocita      79019    TX      US  29.991961   
36                             Pharr      77835    TX      US  26.193348   
37                           Baytown      76581    TX      US  29.732081   
38                     New Braunfels      74587    TX      US  29.709884   
39                     Missouri City      73573    TX      US  29.596162   
40                      Flower Mound      73252    TX      US  33.034065   
41                            Temple      73143    TX      US  31.098237   
42                        Cedar Park      72415    TX      US  30.504857   
43              North Richland Hills      69800    TX      US  32.838869   
44                         Mansfield      67492    TX      US  32.563546   
45                          Victoria      66939    TX      US  28.799192   
46                        Georgetown      66804    TX      US  30.633250   
47                         Harlingen      65449    TX      US  26.190649   
48                           Rowlett      62127    TX      US  32.902706   
49                        San Marcos      61751    TX      US  29.882083   
50                      Pflugerville      59757    TX      US  30.439923   
51                            Spring      58756    TX      US  30.079731   
52  

## Section 2: Creating a map of USA

#### Section 2.1 Obtaining Latitudes and Longitudes for United States

In [28]:
# Use address to get lat and long
address = 'USA'

geolocator = Nominatim(user_agent="CaliforniaTexas")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of USA is {}, {}.'.format(latitude, longitude))

The geograpical coordinate of USA is 39.7837304, -100.4458825.


#### Section 2.2 Creating a map of Caifornia and Texas and superimposed city locations

In [29]:
# create map of USA using latitude and longitude values
Map_CATX= folium.Map(location=[latitude, longitude], zoom_start=4)

# add markers to map
for lat, lng, city, state in zip(CityData['Latitude'], CityData['Longitude'], CityData['City'], CityData['State']):
    label = '{}, {}'.format(city, state)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(Map_CATX)  
    
Map_CATX

#### Section 2.3 Utilizing Foursqaure API 
This section will get the venue information using Foursquare API

In [30]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180604' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WASCKVHUH1MEKSL32EKDDMBRLKTXFTN5CDTNE20CFI504LKX
CLIENT_SECRET:51INCZPGU1FKYN2R2PVYVRE52O0HH15VHPPU3ZZXW0ZC3Q35


Note: Defining a Function to get venues for cities

In [33]:
# Define a function to get the venues in the cities
def getNearbyVenues(names, latitudes, longitudes, state, radius, LIMIT):
    
    venues_list=[] 
    # For each City,State and their Lat and Long
    for name, lat, lng, state in zip(names, latitudes, longitudes, state):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request. Which will give you a json file
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue. To a list
        venues_list.append([(
            state,
            name, 
            lat, 
            lng, 
            v['venue']['name'],
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
    print(venues_list)  
    
    #Putting the results into a data frame
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['State',
                  'City', 
                  'City Latitude', 
                  'City Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [ ]:
# Running the above function for each neighbourhood

CATX_Cities= getNearbyVenues(names=CityData['City'],
                                   latitudes=CityData['Latitude'],
                                   longitudes=CityData['Longitude'],
                                   state = CityData['State'],
                                   radius =1000,
                                   LIMIT = 100
                                  )

In [35]:
print(CATX_Cities.shape)
CATX_Cities.head()

(25084, 8)


State    City  City Latitude  City Longitude                     Venue  \
0    TX  Irving      32.813879      -96.949933         Joe's Coffee Shop   
1    TX  Irving      32.813879      -96.949933           Centennial Park   
2    TX  Irving      32.813879      -96.949933               Di Rosani's   
3    TX  Irving      32.813879      -96.949933         Long John Silvers   
4    TX  Irving      32.813879      -96.949933  Big State Fountain Grill   

   Venue Latitude  Venue Longitude      Venue Category  
0       32.814211       -96.950750         Coffee Shop  
1       32.812088       -96.951211                Park  
2       32.813883       -96.946246         Pizza Place  
3       32.813530       -96.950368  Seafood Restaurant  
4       32.813705       -96.945927            Pharmacy

## Section 3 Understading the cities

#### Section 3.1 Venues per city count. 
I will drop the cities with less than 5 venues as I Use top 5 venues for clustering purpoases.

In [36]:
# how many observation of venues for each city
CATX_Cities.groupby('City').count()

State  City Latitude  City Longitude  Venue  \
City                                                                           
Abilene                             21             21              21     21   
Addison                             35             35              35     35   
Adelanto                             8              8               8      8   
Agoura Hills                        21             21              21     21   
Alameda                             95             95              95     95   
Alamo                               59             59              59     59   
Albany                             100            100             100    100   
Aldine                               7              7               7      7   
Alhambra                            80             80              80     80   
Alice                               18             18              18     18   
Aliso Viejo                         65             65              65     65   
Allen                               62             62              62     62   
Alpine                              27             27              27     27   
Altadena                            27             27              27     27   
Alton                               11             11              11     11   
Alum Rock                           42             42              42     42   
Alvin                               16             16              16     16   
Amarillo                            30             30              30     30   
American Canyon                     25             25              25     25   
Anderson                            22             22              22     22   
Andrews                             14             14              14     14   
Angleton                            12             12              12     12   
Anna                                 7              7               7      7   
Antelope                            21             21              21     21   
Antioch                             17             17              17     17   
Apple Valley                        32             32              32     32   
Arcadia                             52             52              52     52   
Arcata                              45             45              45     45   
Arden-Arcade                        38             38              38     38   
Arroyo Grande                       28             28              28     28   
Artesia                            100            100             100    100   
Arvin                               12             12              12     12   
Ashland                             25             25              25     25   
Atascadero                          33             33              33     33   
Atascocita                          33             33              33     33   
Athens                              30             30              30     30   
Atwater                             34             34              34     34   
Auburn                              55             55              55     55   
Avenal                               6              6               6      6   
Avocado Heights                     19             19              19     19   
Azle                                21             21              21     21   
Azusa                               36             36              36     36   
Bacliff                             12             12              12     12   
Balch Springs                       25             25              25     25   
Baldwin Park                        44             44              44     44   
Banning                             20             20              20     20   
Barstow                             14             14              14     14   
Bay City                            19             19              19     19   
Bay Point                        

In [37]:
print('There are {} uniques categories.'.format(len(CATX_Cities['Venue Category'].unique())))


There are 498 uniques categories.


In [38]:
# Tally up the total venues per city
VenuesperCity = CATX_Cities.groupby('City').count()
print('Original count of cities: {}'.format(len(VenuesperCity.index)))

# Drop cities with inadequate amount of venue data (they skew the clustering results)
VenuesperCity = VenuesperCity[VenuesperCity.Venue < 5]
list(VenuesperCity.index.values)
CATX_Cities = CATX_Cities[~CATX_Cities['City'].isin(list(VenuesperCity.index.values))]

VenuesperCityUpdated = CATX_Cities.groupby('City').count()
print('Count of cities with more than 5 venues: {}'.format(len(VenuesperCityUpdated .index)))

Original count of cities: 702
Count of cities with more than 5 venues: 674


#### Section 3.2 How many unique venue categories ?

In [39]:
print('There are {} uniques categories.'.format(len(CATX_Cities['Venue Category'].unique())))

There are 498 uniques categories.


#### Section 3.3 Analyzing the Cities
I will look at top five venues of each location.

In [40]:
# one hot encoding -  Get dummies based on categories
CATX_onehot = pd.get_dummies(CATX_Cities[['Venue Category']], prefix="", prefix_sep="")

# add City and State column back to dataframe. 
CATX_onehot['City'] = CATX_Cities['City'] 
#CATX_onehot['State'] = CATX_Cities['State'] 

# move City column to the first column - CHECK
fixed_columns = [CATX_onehot.columns[-1]] + list(CATX_onehot.columns[:-1])
CATX_onehot = CATX_onehot[fixed_columns]


print(CATX_onehot.shape)
CATX_onehot.head()


(24987, 498)


Zoo Exhibit  ATM  Accessories Store  Advertising Agency  Afghan Restaurant  \
0            0    0                  0                   0                  0   
1            0    0                  0                   0                  0   
2            0    0                  0                   0                  0   
3            0    0                  0                   0                  0   
4            0    0                  0                   0                  0   

   African Restaurant  Airport  Airport Terminal  Alternative Healer  \
0                   0        0                 0                   0   
1                   0        0                 0                   0   
2                   0        0                 0                   0   
3                   0        0                 0                   0   
4                   0        0                 0                   0   

   American Restaurant  Animal Shelter  Antique Shop  Aquarium  Arcade  \
0                    0               0             0         0       0   
1                    0               0             0         0       0   
2                    0               0             0         0       0   
3                    0               0             0         0       0   
4                    0               0             0         0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Australian Restaurant  Auto Dealership  Auto Garage  Auto Workshop  \
0                      0                0            0              0   
1                      0                0            0              0   
2                      0                0            0              0   
3                      0                0            0              0   
4                      0                0            0              0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0          0           0       0     0    0               0   
1                0          0           0       0     0    0               0   
2                0          0           0       0     0    0               0   
3                0          0           0       0     0    0               0   
4                0          0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bath House  Bay  \
0                 0                 0                   0           0    0   
1                 0                 0                   0           0    0   
2                 0                 0                   0           0    0   
3                 0                 0                   0           0    0   
4                 0                 0                   0           0    0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0      0          0                0         0            0           0   
1      0          0                0         0            0           0   
2      0          0                0         0            0           0   
3      0          0                0         0            0           0   
4      0          0             

In [41]:
# Group rows by city and take the mean of frequency for each category of venues
CATX_grouped = CATX_onehot.groupby('City').mean().reset_index()
print(CATX_grouped.shape)
CATX_grouped.head()

(674, 498)


City  Zoo Exhibit  ATM  Accessories Store  Advertising Agency  \
0       Abilene          0.0  0.0                0.0                 0.0   
1       Addison          0.0  0.0                0.0                 0.0   
2      Adelanto          0.0  0.0                0.0                 0.0   
3  Agoura Hills          0.0  0.0                0.0                 0.0   
4       Alameda          0.0  0.0                0.0                 0.0   

   Afghan Restaurant  African Restaurant  Airport  Airport Terminal  \
0           0.000000                 0.0    0.000          0.000000   
1           0.000000                 0.0    0.000          0.085714   
2           0.000000                 0.0    0.125          0.000000   
3           0.000000                 0.0    0.000          0.000000   
4           0.010526                 0.0    0.000          0.000000   

   Alternative Healer  American Restaurant  Animal Shelter  Antique Shop  \
0                 0.0             0.142857             0.0           0.0   
1                 0.0             0.028571             0.0           0.0   
2                 0.0             0.000000             0.0           0.0   
3                 0.0             0.047619             0.0           0.0   
4                 0.0             0.010526             0.0           0.0   

   Aquarium    Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0.0  0.000000                     0.0     0.047619         0.0   
1       0.0  0.000000                     0.0     0.000000         0.0   
2       0.0  0.000000                     0.0     0.000000         0.0   
3       0.0  0.000000                     0.0     0.000000         0.0   
4       0.0  0.010526                     0.0     0.000000         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0             0.000000                   0.0          0.000000   
1             0.000000                   0.0          0.000000   
2             0.000000                   0.0          0.000000   
3             0.047619                   0.0          0.000000   
4             0.000000                   0.0          0.021053   

   Athletics & Sports  Australian Restaurant  Auto Dealership  Auto Garage  \
0                 0.0                    0.0              0.0          0.0   
1                 0.0                    0.0              0.0          0.0   
2                 0.0                    0.0              0.0          0.0   
3                 0.0                    0.0              0.0          0.0   
4                 0.0                    0.0              0.0          0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Bagel Shop    Bakery  Bank  \
0            0.0         0.047619        0.0         0.0  0.047619   0.0   
1            0.0         0.000000        0.0         0.0  0.000000   0.0   
2            0.0         0.000000        0.0         0.0  0.000000   0.0   
3            0.0         0.000000        0.0         0.0  0.000000   0.0   
4            0.0         0.010526        0.0         0.0  0.021053   0.0   

        Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0  0.000000             0.0               0.0               0.0   
1  0.028571             0.0               0.0               0.0   
2  0.000000             0.0               0.0               0.0   
3  0.000000             0.0               0.0               0.0   
4  0.021053             0.0               0.0               0.0   

   Basketball Stadium  Bath House  Bay  Beach  Beach Bar  Bed & Breakfast  \
0                 0.0         0.0  0.0    0.0        0.0              0.0   
1                 0.0         0.0  0.0    0.0        0.0              0.0   
2                 0.0         0.0  0.0    0.0        0.0              0.0   
3                 0.0         0.0  0.0    0.0        0.0              0.0   
4                 0.0         0.0  0.0    0.0        0.0              0.0   

   Beer Bar  Beer Garden  Beer Store

In [42]:
# Getting top 5 venues of each city

num_top_venues = 5

for citi in CATX_grouped['City']:
    print("----"+citi+"----")
    temp = CATX_grouped[CATX_grouped['City'] == citi].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abilene----
                 venue  freq
0  American Restaurant  0.14
1    Convention Center  0.05
2       History Museum  0.05
3          Music Venue  0.05
4    Indian Restaurant  0.05


----Addison----
                 venue  freq
0     Airport Terminal  0.09
1                 Park  0.09
2   Italian Restaurant  0.06
3   Mexican Restaurant  0.06
4  Rental Car Location  0.06


----Adelanto----
                venue  freq
0         Pizza Place  0.12
1      Discount Store  0.12
2               Hotel  0.12
3  Mexican Restaurant  0.12
4             Airport  0.12


----Agoura Hills----
                 venue  freq
0                Hotel  0.10
1   Italian Restaurant  0.05
2  Arts & Crafts Store  0.05
3          Pizza Place  0.05
4             Pharmacy  0.05


----Alameda----
                venue  freq
0         Pizza Place  0.05
1  Mexican Restaurant  0.03
2       Grocery Store  0.03
3                Café  0.03
4                Park  0.03


----Alamo----
                  venue  freq
0 

In [43]:
# function to sort venues in decending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [46]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['City']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
CATX_venues_sorted = pd.DataFrame(columns=columns)
CATX_venues_sorted['City'] = CATX_grouped['City']

for ind in np.arange(CATX_grouped.shape[0]):
    CATX_venues_sorted.iloc[ind, 1:] = return_most_common_venues(CATX_grouped.iloc[ind, :], num_top_venues)

CATX_venues_sorted.head()

City 1st Most Common Venue 2nd Most Common Venue  \
0       Abilene   American Restaurant     Convention Center   
1       Addison                  Park      Airport Terminal   
2      Adelanto           Pizza Place               Airport   
3  Agoura Hills                 Hotel    Italian Restaurant   
4       Alameda           Pizza Place         Grocery Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0             Rock Club        History Museum                Bakery  
1                 Plaza    Mexican Restaurant   Rental Car Location  
2           Video Store                 Hotel        Discount Store  
3           Pizza Place                   Gym                  Park  
4    Mexican Restaurant                  Café                  Park

## Section 4: Clustering

#### Section 4.1 Creating the clusters using K-mean clustering. Number of cluster is 5

In [47]:
# set number of clusters
kclusters =5

CATX_grouped_clustering = CATX_grouped.drop('City', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(CATX_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 


array([2, 2, 3, 2, 2, 0, 2, 2, 2, 0])

In [48]:
# add clustering labels
CATX_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

CATX_merged = CityData

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
CATX_merged = CATX_merged.join(CATX_venues_sorted.set_index('City'), on='City')

CATX_merged.tail() # check the last columns!

City Population State Country   Latitude   Longitude  \
709     Anderson      10265    CA      US  40.450409 -122.301460   
710  Quartz Hill      10164    CA      US  34.647400 -118.218450   
711  Shasta Lake      10142    CA      US  40.681072 -122.372208   
712     Capitola      10135    CA      US  36.973068 -121.952033   
713     Del Aire      10065    CA      US  33.909475 -118.367087   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
709             0.0  Fast Food Restaurant           Pizza Place   
710             2.0                   Bar    Mexican Restaurant   
711             3.0         Grocery Store           Pizza Place   
712             2.0        Ice Cream Shop    Mexican Restaurant   
713             0.0  Fast Food Restaurant    Mexican Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
709   American Restaurant          Intersection                 Hotel  
710    Italian Restaurant           Pizza Place           Coffee Shop  
711   American Restaurant            Food Truck           Coffee Shop  
712                 Hotel   American Restaurant    Italian Restaurant  
713     Mobile Phone Shop            Laundromat                  Park

#### Section 4.2 Cleaning the result
1. Convert cluster lables to integers for maping purposes
2. Drop any NA values

In [49]:
CATX_merged = CATX_merged.dropna()
# Making cluster a integer
CATX_merged['Cluster Labels'] = CATX_merged['Cluster Labels'].astype(int)
CATX_merged.tail()

City Population State Country   Latitude   Longitude  \
709     Anderson      10265    CA      US  40.450409 -122.301460   
710  Quartz Hill      10164    CA      US  34.647400 -118.218450   
711  Shasta Lake      10142    CA      US  40.681072 -122.372208   
712     Capitola      10135    CA      US  36.973068 -121.952033   
713     Del Aire      10065    CA      US  33.909475 -118.367087   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
709               0  Fast Food Restaurant           Pizza Place   
710               2                   Bar    Mexican Restaurant   
711               3         Grocery Store           Pizza Place   
712               2        Ice Cream Shop    Mexican Restaurant   
713               0  Fast Food Restaurant    Mexican Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
709   American Restaurant          Intersection                 Hotel  
710    Italian Restaurant           Pizza Place           Coffee Shop  
711   American Restaurant            Food Truck           Coffee Shop  
712                 Hotel   American Restaurant    Italian Restaurant  
713     Mobile Phone Shop            Laundromat                  Park

#### Section 4.3 Creating the cluster map

In [52]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(CATX_merged['Latitude'], CATX_merged['Longitude'], CATX_merged['City'], CATX_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

#### Step 3.7: Understanding the Clusters

##### Cluster 1 -------------------------

In [69]:
df_Cluster1 = CATX_merged.loc[CATX_merged['Cluster Labels'] == 0, CATX_merged.columns[[0]  + list(range(4, CATX_merged.shape[1]))]]
df_Cluster1

City   Latitude   Longitude  Cluster Labels  \
0                      Irving  32.813879  -96.949933               0   
1                     Garland  32.914343  -96.636564               0   
3               Grand Prairie  32.745496  -97.003529               0   
14                 Carrollton  32.975541  -96.889788               0   
20                   Pearland  29.563689  -95.286096               0   
29                      Allen  33.104193  -96.671738               0   
33                   Longview  32.494556  -94.742336               0   
34                     Conroe  30.313044  -95.458141               0   
35                 Atascocita  29.991961  -95.182162               0   
39              Missouri City  29.596162  -95.526747               0   
48                    Rowlett  32.902706  -96.569287               0   
53                     Euless  32.837287  -97.082685               0   
54                     DeSoto  32.589734  -96.853048               0   
58                      Wylie  33.013834  -96.536679               0   
61                    Leander  30.578661  -97.852863               0   
64                Haltom City  32.809091  -97.264576               0   
75                Friendswood  29.528515  -95.200012               0   
76               Mission Bend  29.700211  -95.647386               0   
77                  Lancaster  32.600720  -96.784557               0   
80                  Texarkana  33.442210  -94.064080               0   
84                     Lufkin  31.332913  -94.727903               0   
88                  Deer Park  29.700047  -95.113603               0   
91              Copperas Cove  31.115040  -97.905488               0   
93             Harker Heights  31.061308  -97.652139               0   
94                   Cleburne  32.346612  -97.387309               0   
97                 Big Spring  32.240415 -101.472454               0   
99                     Cibolo  29.576651  -98.237690               0   
103                  Converse  29.515414  -98.312210               0   
107                Kingsville  27.506723  -97.855992               0   
109             Balch Springs  32.728477  -96.622613               0   
110                    Sachse  32.973287  -96.590589               0   
117                San Benito  26.138190  -97.626124               0   
122                  Marshall  32.545002  -94.363315               0   
123                 Kerrville  30.042787  -99.135299               0   
124                  Benbrook  32.679121  -97.464135               0   
128                 Plainview  34.192454 -101.723218               0   
129                 Dickinson  29.460726  -95.051812               0   
132            Universal City  29.552827  -98.306660               0   
134                     Alamo  26.188087  -98.122451               0   
139                     Alice  27.755128  -98.064771               0   
147                     Pampa  35.533444 -100.971880               0   
148                  Bay City  28.981885  -95.970000               0   
151                   Terrell  32.736812  -96.280661               0   
152                 Nederland  29.963772  -93.999412               0   
158               Pecan Grove  29.623288  -95.741141               0   
159                  Mercedes  26.149094  -97.921709               0   
164                    Uvalde  29.210991  -99.786769               0   
165               Gainesville  33.624221  -97.133371               0   
167            Mount Pleasant  33.156684  -94.968574               0   
169                    Humble  29.999022  -95.261315               0   
175                   Crowley  32.578396  -97.353249               0   
179                   Kilgore  32.385785  -94.868573               0   
183                     Dumas  35.865393 -101.973221               0   
187                   Hidalgo  26.104421  -98.257735               0   
188                 Levelland  33.587855 -102.365124             

##### Map of Cluster 1

In [73]:
map_clusters_1 = folium.Map(location=[latitude, longitude], zoom_start=11)
for lat, lon, poi in zip(df_Cluster1['Latitude'], df_Cluster1['Longitude'], df_Cluster1['City']):
    label = folium.Popup(str(poi), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_1)
       
map_clusters_1

##### Cluster 2 ----------------------

In [74]:
df_Cluster2 = CATX_merged.loc[CATX_merged['Cluster Labels'] == 1, CATX_merged.columns[[0]  + list(range(4, CATX_merged.shape[1]))]]
df_Cluster2

City   Latitude   Longitude  Cluster Labels  \
81           San Juan city  30.627248  -97.815648               1   
85          Farmers Branch  32.933002  -96.873089               1   
115                 Fresno  29.535818  -95.466638               1   
143               Bellaire  29.704482  -95.455438               1   
163       Highland Village  33.084913  -97.054250               1   
173  West University Place  29.715981  -95.428839               1   
201          Glenn Heights  32.560764  -96.852222               1   
314              Livermore  37.675914 -121.758862               1   
389                 Santee  32.871379 -116.971181               1   
400         Cathedral City  33.830493 -116.466872               1   
421            San Jacinto  33.783905 -116.958870               1   
426        El Dorado Hills  38.682094 -121.075814               1   
440              La Quinta  33.665397 -116.307975               1   
465          Beverly Hills  34.080294 -118.404679               1   
468             Dana Point  33.480878 -117.697659               1   
472         Foothill Farms  38.670798 -121.336871               1   
490           Ladera Ranch  33.550315 -117.637425               1   
514          Paradise town  39.752081 -121.621973               1   
545  West Rancho Dominguez  33.893213 -118.265398               1   
573           Cameron Park  38.680741 -120.994440               1   
613          Discovery Bay  37.908652 -121.600400               1   
617                Parkway  38.507780 -121.450458               1   
620         Mountain House  37.783796 -121.545264               1   
632           Coto de Caza  33.573853 -117.590753               1   
634                 Kerman  36.721590 -120.060062               1   
646               Oak Park  34.170860 -118.758432               1   
690               Piedmont  37.826265 -122.232871               1   
699             La Riviera  38.562547 -121.359463               1   
708               Fairview  37.678786 -122.050812               1   

          1st Most Common Venue       2nd Most Common Venue  \
81   Construction & Landscaping                        Park   
85                         Park         American Restaurant   
115           Convenience Store  Construction & Landscaping   
143                        Park               Deli / Bodega   
163                        Park                 IT Services   
173                        Park                  Playground   
201            Storage Facility                 Gas Station   
314                        Park              Farmers Market   
389  Construction & Landscaping           Martial Arts Dojo   
400                Home Service  Construction & Landscaping   
421                        Park           Convenience Store   
426                Home Service                        Park   
440                       Trail                        Park   
465                        Park                 Coffee Shop   
468                        Park         Sporting Goods Shop   
472                        Park           Convenience Store   
490                        Park                        Pool   
514                 Coffee Shop            Insurance Office   
545                        Park                  Bagel Shop   
573  Construction & Landscaping                        Food   
613            Insurance Office              Ice Cream Shop   
617                Intersection           Indian Restaurant   
620                        Park                       Trail   
632              Baseball Field              Sandwich Place   
634                        Park              Baseball Field   
646              Clothing Store                        Park   
690                        Park                     Dog Run   
699                        Park           Convenience Store   
708  Construction & Landscaping                        Park   

    3rd Most Common Venue   4th Most Common Venue       5th 

In [76]:
map_clusters_2 = folium.Map(location=[latitude, longitude], zoom_start=11)
for lat, lon, poi in zip(df_Cluster2['Latitude'], df_Cluster2['Longitude'], df_Cluster2['City']):
    label = folium.Popup(str(poi), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-2],
        fill=True,
        fill_color=rainbow[cluster-2],
        fill_opacity=0.7).add_to(map_clusters_2)
       
map_clusters_2

### Cluster 3 ---------------------

In [85]:
df_Cluster3 = CATX_merged.loc[CATX_merged['Cluster Labels'] == 2, CATX_merged.columns[[0]  + list(range(4, CATX_merged.shape[1]))]]
df_Cluster3

City   Latitude   Longitude  Cluster Labels  \
2                           Amarillo  35.207009 -101.832013               2   
5                           McKinney  33.197963  -96.615024               2   
6                             Frisco  33.150660  -96.825082               2   
7                           Pasadena  29.693379  -95.193333               2   
10                           McAllen  26.196695  -98.235698               2   
12                              Waco  31.556767  -97.129989               2   
13                            Denton  33.215533  -97.132450               2   
15                           Abilene  32.453562  -99.732654               2   
16                        Round Rock  30.508556  -97.678805               2   
17                          Beaumont  30.086170  -94.102012               2   
19                        Sugar Land  29.597075  -95.620971               2   
21                        Richardson  32.960761  -96.733518               2   
22                   College Station  30.622373  -96.325850               2   
23                     The Woodlands  30.182039  -95.484612               2   
24                        Lewisville  33.046344  -96.994166               2   
25                     Wichita Falls  33.909760  -98.500854               2   
26                             Tyler  32.350763  -95.300644               2   
27                       League City  29.507507  -95.095204               2   
28                        San Angelo  31.463780 -100.437304               2   
32                             Bryan  30.670524  -96.370542               2   
37                           Baytown  29.732081  -94.967821               2   
38                     New Braunfels  29.709884  -98.119725               2   
40                      Flower Mound  33.034065  -97.079639               2   
41                            Temple  31.098237  -97.342737               2   
43              North Richland Hills  32.838869  -97.214266               2   
44                         Mansfield  32.563546  -97.142032               2   
45                          Victoria  28.799192  -97.006062               2   
46                        Georgetown  30.633250  -97.676978               2   
49                        San Marcos  29.882083  -97.939985               2   
50                      Pflugerville  30.439923  -97.620959               2   
51                            Spring  30.079731  -95.417690               2   
52                       Port Arthur  29.872307  -93.934199               2   
55                         Grapevine  32.939862  -97.078367               2   
56                         Galveston  29.300128  -94.795846               2   
57                           Bedford  32.844252  -97.143237               2   
59                        Cedar Hill  32.589903  -96.954231               2   
62                            Keller  32.934631  -97.253647               2   
65                          Rockwall  32.931051  -96.458650               2   
67                        The Colony  33.096465  -96.887014               2   
69                           Coppell  32.961238  -96.993469               2   
70                           Sherman  33.635590  -96.609017               2   
71                        Huntsville  30.720391  -95.551435               2   
82                         Rosenberg  29.558248  -95.808826               2   
90                       Nacogdoches  31.603869  -94.656017               2   
92                         Southlake  32.941061  -97.133584               2   
95                       Weatherford  32.757462  -97.814529               2   
105                      Colleyville  32.883432  -97.153892               2   
108                        Fort Hood  31.133063  -97.766923               2   
112                  University Park  32.851576  -96.794950               2   
116                          Watauga  32.874127  -97.255030               2   
118

In [88]:
map_clusters_3 = folium.Map(location=[latitude, longitude], zoom_start=4)
for lat, lon, poi in zip(df_Cluster3['Latitude'], df_Cluster3['Longitude'], df_Cluster3['City']):
    label = folium.Popup(str(poi), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-3],
        fill=True,
        fill_color=rainbow[cluster-3],
        fill_opacity=0.7).add_to(map_clusters_3)
       
map_clusters_3

### Cluster 4 ----------------------

In [82]:
df_Cluster4 = CATX_merged.loc[CATX_merged['Cluster Labels'] == 3, CATX_merged.columns[[0]  + list(range(4, CATX_merged.shape[1]))]]
df_Cluster4

City   Latitude   Longitude  Cluster Labels  \
8       Mesquite city  30.270170  -98.404080               3   
9             Killeen  31.117810  -97.731129               3   
31            Mission  26.212384  -98.318152               3   
60         Texas City  29.384016  -94.902549               3   
74        Duncanville  32.645162  -96.905300               3   
79              Hurst  32.823635  -97.179341               3   
100      Lake Jackson  29.036192  -95.448867               3   
101        Greenville  33.139083  -96.107237               3   
114             Paris  33.661426  -95.556321               3   
121         Corsicana  32.084920  -96.464976               3   
138             Ennis  32.325061  -96.632740               3   
161             Alton  26.287080  -98.313631               3   
171            Groves  29.946525  -93.918815               3   
177     Mineral Wells  32.809204  -98.112938               3   
186            Hewitt  31.462170  -97.195726               3   
200         Lumberton  30.265908  -94.199786               3   
215          El Campo  29.196740  -96.269884               3   
232        Sweetwater  32.470612 -100.407381               3   
325             Hemet  33.747562 -116.967316               3   
365   Florence-Graham  33.967440 -118.247683               3   
415   North Highlands  38.687868 -121.369445               3   
464           Oildale  35.419586 -119.021274               3   
474          Adelanto  34.582826 -117.414029               3   
564        East Hemet  33.740493 -116.932483               3   
578         Prunedale  36.801310 -121.660957               3   
583             Linda  39.127626 -121.555578               3   
615  East San Gabriel  34.113497 -118.082847               3   
626         Clearlake  38.961814 -122.631261               3   
630        Susanville  40.415483 -120.648932               3   
680             Delhi  37.430829 -120.776970               3   
685  Lake Los Angeles  34.618159 -117.826923               3   
693            Newman  37.317156 -121.023357               3   
702      Garden Acres  37.959241 -121.230073               3   
711       Shasta Lake  40.681072 -122.372208               3   

    1st Most Common Venue 2nd Most Common Venue       3rd Most Common Venue  \
8           Grocery Store    Mexican Restaurant         American Restaurant   
9             Pizza Place         Grocery Store           Korean Restaurant   
31           Burger Joint     Convenience Store         Fried Chicken Joint   
60         Clothing Store               Brewery                  Smoke Shop   
74         Discount Store    Chinese Restaurant            Business Service   
79            Pizza Place          Optical Shop                Antique Shop   
100   American Restaurant           Pizza Place                 Wings Joint   
101                   Bar   American Restaurant         Fried Chicken Joint   
114         Grocery Store          Dessert Shop              Sandwich Place   
121           Pizza Place              Pharmacy        Fast Food Restaurant   
138         Grocery Store   American Restaurant          Mexican Restaurant   
161        Discount Store          Burger Joint        Fast Food Restaurant   
171    Italian Restaurant         Grocery Store              Discount Store   
177     Convenience Store           Pizza Place      Furniture / Home Store   
186            Donut Shop           Pizza Place               Grocery Store   
200          Burger Joint   American Restaurant              Sandwich Place   
215   American Restaurant        Ice Cream Shop                    Pharmacy   
232        Sandwich Place          Liquor Store                Burger Joint   
325   American Restaurant              Pharmacy              Sandwich Place   
365          Burger Joint    Mexican Restaurant               Grocery Store   
415         Grocery Store            Shoe Store          Mexican Restaurant   
464           Pizza Place   American R

In [83]:
map_clusters_4 = folium.Map(location=[latitude, longitude], zoom_start=4)
for lat, lon, poi in zip(df_Cluster4['Latitude'], df_Cluster4['Longitude'], df_Cluster4['City']):
    label = folium.Popup(str(poi), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-4],
        fill=True,
        fill_color=rainbow[cluster-4],
        fill_opacity=0.7).add_to(map_clusters_4)
       
map_clusters_4

### Cluster 5 ----------------------

In [77]:
df_Cluster5 = CATX_merged.loc[CATX_merged['Cluster Labels'] == 4, CATX_merged.columns[[0]  + list(range(4, CATX_merged.shape[1]))]]
df_Cluster5

City   Latitude   Longitude  Cluster Labels  \
4                Brownsville  25.903046  -97.498884               4   
11                   Midland  31.997433 -102.078043               4   
18                    Odessa  31.849462 -102.374677               4   
30                  Edinburg  26.299359  -98.162704               4   
36                     Pharr  26.193348  -98.184175               4   
42                Cedar Park  30.504857  -97.819854               4   
47                 Harlingen  26.190649  -97.696108               4   
63                  Burleson  32.545038  -97.327316               4   
66                Little Elm  33.161632  -96.936073               4   
72                   Weslaco  26.161532  -97.982648               4   
73                      Kyle  29.987408  -97.874273               4   
78                   Schertz  29.555069  -98.263612               4   
83                   Del Rio  29.365723 -100.897922               4   
86                  La Porte  29.664164  -95.019283               4   
87                Waxahachie  32.393610  -96.846992               4   
96                Eagle Pass  28.706045 -100.500457               4   
98                    Seguin  29.580782  -97.968526               4   
104                    Alvin  29.423834  -95.244078               4   
106          Timberwood Park  29.711979  -98.479385               4   
111              Canyon Lake  29.879946  -98.200264               4   
113               Cloverleaf  29.780027  -95.169688               4   
119               Midlothian  32.482209  -96.994499               4   
125                  Saginaw  32.860222  -97.363920               4   
127                   Belton  31.056417  -97.463763               4   
131             Stephenville  32.220657  -98.202145               4   
137                   Forney  32.752075  -96.472348               4   
145                 Stafford  29.616014  -95.556901               4   
146                     Katy  29.794857  -95.816531               4   
150         White Settlement  32.758840  -97.459054               4   
155                 Portland  27.876706  -97.327429               4   
160                    Donna  26.170700  -98.054279               4   
166                La Marque  29.368517  -94.971739               4   
180             Jacksonville  31.963447  -95.270455               4   
181                   Boerne  29.802767  -98.734923               4   
184                     Buda  30.082665  -97.842482               4   
185          Rio Grande City  26.380070  -98.825375               4   
192                  Andrews  32.319034 -102.545408               4   
203               Gatesville  31.434024  -97.744311               4   
205              Port Lavaca  28.614812  -96.626153               4   
209                 Freeport  28.953725  -95.358504               4   
210                 Richmond  29.576349  -95.765327               4   
212              Trophy Club  32.994958  -97.188411               4   
219                 Robstown  27.798176  -97.659089               4   
220                   Snyder  32.716152 -100.917190               4   
229          Fair Oaks Ranch  29.725757  -98.641598               4   
231             Jacinto City  29.767596  -95.240419               4   
234                  Bacliff  29.507422  -94.989349               4   
238                 Pearsall  28.889431  -99.097074               4   
246                   Oxnard  34.197663 -119.175947               4   
247            Moreno Valley  33.917114 -117.261144               4   
254                  Ontario  34.063341 -117.651187               4   
256                   Corona  33.875665 -117.568843               4   
259                 Palmdale  34.576469 -118.116103               4   
277         East Los Angeles  34.033370 -118.162815               4   
285                  Antioch  38.016907 -121.813771               4   
288                 Richmond  37.937865 -122.343

In [81]:
map_clusters_5 = folium.Map(location=[latitude, longitude], zoom_start=4)
for lat, lon, poi in zip(df_Cluster5['Latitude'], df_Cluster5['Longitude'], df_Cluster5['City']):
    label = folium.Popup(str(poi), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-5],
        fill=True,
        fill_color=rainbow[cluster-5],
        fill_opacity=0.7).add_to(map_clusters_5)
       
map_clusters_5

#### END